In [2]:
!pip install trimesh

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 712.0/712.0 kB 40.1 MB/s eta 0:00:00


In [18]:
import json
import trimesh
import numpy as np
import uuid
from pathlib import Path

# ------------ CONFIG ------------
CITYWEFT_FILE = "/content/test-json-n8n.json"  # Your uploaded file path
OUTPUT_FILE = "infrared_ready.json"
# --------------------------------

# 1. Load CityWeft file
data = json.loads(Path(CITYWEFT_FILE).read_text())

# 2. Extract & process all meshes from all entries
infrared_geometries = {}
mesh_counter = 0
skipped_meshes = 0

for i, item in enumerate(data):
    geometries = item.get("geometry", [])
    if not geometries or not isinstance(geometries, list):
        print(f"⚠️ Skipping item {i}: missing or invalid 'geometry'")
        continue

    for j, geo in enumerate(geometries):
        meshes = geo.get("meshes", [])
        if not meshes or not isinstance(meshes, list):
            print(f"⚠️ Skipping geometry {j} in item {i}: missing or invalid 'meshes'")
            continue

        for k, mesh_data in enumerate(meshes):
            # Skip fences or other unwanted types
            descriptor = mesh_data.get("descriptor", {})
            if descriptor.get("type") == "fence":
                print(f"⏭️ Skipping item {i}, geometry {j}, mesh {k}: type is 'fence'")
                skipped_meshes += 1
                continue

            raw_vertices = mesh_data.get("vertices")
            if not isinstance(raw_vertices, list) or len(raw_vertices) % 3 != 0:
                print(f"❌ Skipping item {i}, geometry {j}, mesh {k}: invalid vertices")
                skipped_meshes += 1
                continue

            try:
                verts = np.array(raw_vertices).reshape(-1, 3)
                mesh = trimesh.Trimesh(vertices=verts, process=True)
                hull = mesh.convex_hull

                coords = hull.vertices.flatten().tolist()
                faces = hull.faces.flatten().tolist()

                infrared_geometries[str(uuid.uuid4())] = {
                    "coordinates": coords,
                    "indexes": faces
                }

                print(f"✅ Processed item {i}, geometry {j}, mesh {k} → {len(hull.faces)} faces")
                mesh_counter += 1

            except Exception as e:
                print(f"❌ Error in item {i}, geometry {j}, mesh {k}: {e}")
                skipped_meshes += 1

# 3. Save result
with open(OUTPUT_FILE, "w") as f:
    json.dump(infrared_geometries, f, indent=2)

print(f"\n✅ Saved {mesh_counter} meshes to {OUTPUT_FILE}")
print(f"⚠️ Skipped {skipped_meshes} meshes due to errors")


✅ Processed item 0, geometry 0, mesh 0 → 40 faces
✅ Processed item 0, geometry 0, mesh 1 → 28 faces
✅ Processed item 0, geometry 0, mesh 2 → 44 faces
✅ Processed item 0, geometry 0, mesh 3 → 20 faces
✅ Processed item 0, geometry 0, mesh 4 → 16 faces
✅ Processed item 0, geometry 0, mesh 5 → 16 faces
✅ Processed item 0, geometry 0, mesh 6 → 20 faces
✅ Processed item 0, geometry 0, mesh 7 → 24 faces
✅ Processed item 0, geometry 0, mesh 8 → 20 faces
✅ Processed item 0, geometry 0, mesh 9 → 28 faces
✅ Processed item 0, geometry 0, mesh 10 → 20 faces
✅ Processed item 0, geometry 0, mesh 11 → 24 faces
✅ Processed item 0, geometry 0, mesh 12 → 24 faces
✅ Processed item 0, geometry 0, mesh 13 → 32 faces
✅ Processed item 0, geometry 0, mesh 14 → 20 faces
✅ Processed item 0, geometry 0, mesh 15 → 36 faces
✅ Processed item 0, geometry 0, mesh 16 → 28 faces
✅ Processed item 0, geometry 0, mesh 17 → 40 faces
✅ Processed item 0, geometry 0, mesh 18 → 16 faces
✅ Processed item 0, geometry 0, mesh 19 →

In [21]:
print(json.dumps(infrared_geometries, indent=2))


{
  "d09520c1-e238-420a-8f20-acd703ae18cb": {
    "coordinates": [
      -200.47775707619283,
      20.0,
      93.42239782144684,
      -269.774487720505,
      20.0,
      110.1483944823045,
      -265.1283817579455,
      20.0,
      143.27516304587826,
      -203.82296400618606,
      20.0,
      91.49426061791041,
      -271.54001254497064,
      20.0,
      113.12187798531313,
      -257.6249060026051,
      20.0,
      171.87195835167452,
      -246.0096410962063,
      20.0,
      207.69348432895836,
      -143.49322052885134,
      20.0,
      233.61877155546605,
      -201.77867510331336,
      20.0,
      91.912406735521,
      -217.94712461280264,
      20.0,
      95.28082501082723,
      -271.0521754077583,
      20.0,
      111.4725428492923,
      -200.47775707619283,
      0.0,
      93.42239782144684,
      -201.77867510331336,
      0.0,
      91.912406735521,
      -143.49322052885134,
      0.0,
      233.61877155546605,
      -246.0096410962063,
      0.0,
      2

In [29]:
analysis_payload = {
    "analysis-type": "wind-comfort",
    "wind-speed": 15,
    "wind-direction": 35,
    "geometries":{
        "25f551cd-f80e-4b18-9d71-f9fd5a46eacf":{
            "coordinates":[
                0,
                0,
                0,
                1,
                0,
                0,
                1,
                1,
                0,
                0,
                1,
                0
            ],
            "indexes":[
                0,
                2,
                1,
                0,
                3,
                2
            ]
        },
        "6d094c39-cc8a-4394-b8c6-9d63c427fe75":{
            "coordinates":[
                5,
                5,
                5,
                6,
                5,
                5,
                6,
                6,
                5,
                5,
                6,
                5
            ],
            "indexes":[
                0,
                2,
                1,
                0,
                3,
                2
            ]
        }
    }
}

In [30]:
print(analysis_payload)

{'analysis-type': 'wind-comfort', 'wind-speed': 15, 'wind-direction': 35, 'geometries': {'25f551cd-f80e-4b18-9d71-f9fd5a46eacf': {'coordinates': [0, 0, 0, 1, 0, 0, 1, 1, 0, 0, 1, 0], 'indexes': [0, 2, 1, 0, 3, 2]}, '6d094c39-cc8a-4394-b8c6-9d63c427fe75': {'coordinates': [5, 5, 5, 6, 5, 5, 6, 6, 5, 5, 6, 5], 'indexes': [0, 2, 1, 0, 3, 2]}}}


In [31]:
import requests
import base64
import zlib
import json
import gzip

url = "https://fbiw2nq5ac.execute-api.eu-central-1.amazonaws.com/development-v1/api/run-analysis"

# Load ready geometry
with open("/content/infrared_ready.json", "r") as f:
    infrared_geometries = json.load(f)

# # Prepare payload
# analysis_payload = {
#     "analysis-type": "wind-comfort",
#     "wind-speed": 15,
#     "wind-direction": 35,
#     "geometries": infrared_geometries
# }

json_string=json.dumps(analysis_payload)

# Compress the JSON string using Gzip and then base64
compressed_data = gzip.compress(json_string.encode('utf-8'))
base64_encoded = base64.b64encode(compressed_data).decode('utf-8')

# Headers
headers = {
      "x-api-key":"AEPcDGeNCw4x6M97zfowL1dzNKkiagNJ7OzyftkO",
      "Content-Type": "text/plain",
      "X-Infrared-Encoding": "gzip",
  }

# Send request
response = requests.post(url, data=base64_encoded, headers=headers)


# Save result
if response.status_code == 200:
    with open("infrared_final.json", "w") as f:
        json.dump(response.json(), f, indent=2)
    print("✅ Infrared analysis complete. Results saved to infrared_final.json")
else:
    print("❌ Infrared API Error:", response.status_code, response.text)


❌ Infrared API Error: 500 {"message":"Error running inference: Received client error (400) from primary with message \"{\"error\":\"Failed to process the request(s) for model instance 'global-cfd-v3.tar.gz_0', message: Exception: Failed to load mesh. Error: 'indices'\\n\\nAt:\\n  /opt/ml/models/297dab694a2f3823e46e0f28f00fa71f/model/cfd-pix2pix/1/InfraredEncoders/encoders.py(227): create_mesh_from_string\\n  /opt/ml/models/297dab694a2f3823e46e0f28f00fa71f/model/cfd-pix2pix/1/InfraredEncoders/encoders.py(157): __init__\\n  /opt/ml/models/297dab694a2f3823e46e0f28f00fa71f/model/cfd-pix2pix/1/InfraredEncoders/encoders.py(196): __init__\\n  /opt/ml/models/297dab694a2f3823e46e0f28f00fa71f/model/cfd-pix2pix/1/model.py(189): execute\\n\"}\". See https://eu-central-1.console.aws.amazon.com/cloudwatch/home?region=eu-central-1#logEventViewer:group=/aws/sagemaker/Endpoints/multimodel-test-env19 in account 471112737537 for more information."}
